## Train a character-level GPT on some text data

The inputs here are simple text files, which we chop up to individual characters and then train GPT on. So you could say this is a char-transformer instead of a char-rnn. Doesn't quite roll off the tongue as well. In this example we will feed it some Shakespeare, which we'll get it to predict character-level.

In [1]:
import numpy as np
from os import listdir
from os.path import join as pathjoin
import torch
import torch.nn as nn
from torch.nn import functional as F
import tqdm

from mingpt.model import GPT, GPTConfig
from mingpt.trainer import Trainer, TrainerConfig
# make deterministic
from mingpt.utils import sample, set_seed
set_seed(42)

In [2]:
import math
from torch.utils.data import Dataset

class CharDataset(Dataset):

    def __init__(self, data, block_size):
        chars = sorted(list(set(data)))
        data_size, vocab_size = len(data), len(chars)
        print('data has %d characters, %d unique.' % (data_size, vocab_size))
        
        self.stoi = { ch:i for i,ch in enumerate(chars) }
        self.itos = { i:ch for i,ch in enumerate(chars) }
        self.block_size = block_size
        self.vocab_size = vocab_size
        self.data = data
    
    def __len__(self):
        return len(self.data) - self.block_size

    def __getitem__(self, idx):
        # grab a chunk of (block_size + 1) characters from the data
        chunk = self.data[idx:idx + self.block_size + 1]
        # encode every character to an integer
        dix = [self.stoi[s] for s in chunk]
        """
        arrange data and targets so that the first i elements of x
        will be asked to predict the i-th element of y. Notice that
        the eventual language model will actually make block_size
        individual predictions at the same time based on this data,
        so we are being clever and amortizing the cost of the forward
        pass of the network. So for example if block_size is 4, then
        we could e.g. sample a chunk of text "hello", the integers in
        x will correspond to "hell" and in y will be "ello". This will
        then actually "multitask" 4 separate examples at the same time
        in the language model:
        - given just "h", please predict "e" as next
        - given "he" please predict "l" next
        - given "hel" predict "l" next
        - given "hell" predict "o" next
        
        In addition, because the DataLoader will create batches of examples,
        every forward/backward pass during traning will simultaneously train
        a LOT of predictions, amortizing a lot of computation. In particular,
        for a batched input of integers X (B, T) where B is batch size and
        T is block_size and Y (B, T), the network will during training be
        simultaneously training to make B*T predictions, all at once! Of course,
        at test time we can paralellize across batch B, but unlike during training
        we cannot parallelize across the time dimension T - we have to run
        a forward pass of the network to recover the next single character of the 
        sequence along each batch dimension, and repeatedly always feed in a next
        character to get the next one.
        
        So yes there is a big asymmetry between train/test time of autoregressive
        models. During training we can go B*T at a time with every forward pass,
        but during test time we can only go B at a time, T times, with T forward 
        passes.
        """
        x = torch.tensor(dix[:-1], dtype=torch.long)
        y = torch.tensor(dix[1:], dtype=torch.long)
        return x, y


In [3]:
block_size = 128

In [4]:
def train_gpt_generator(train_text_file, state_dict_file, n_layer=8, n_head=8, n_embd=512,
                        max_epochs=2, batch_size=512):
    text = open(train_text_file, 'r').read()
    train_dataset = CharDataset(text, block_size) 
    mconf = GPTConfig(
        train_dataset.vocab_size, train_dataset.block_size,
        n_layer=n_layer, n_head=n_head, n_embd=n_embd
    )
    model = GPT(mconf)
    tconf = TrainerConfig(
        max_epochs=max_epochs, batch_size=batch_size, learning_rate=6e-4,
        lr_decay=True, warmup_tokens=batch_size*20, final_tokens=2*len(train_dataset)*block_size,
        num_workers=4
    )
    trainer = Trainer(model, train_dataset, None, tconf)
    trainer.train()
    torch.save(model.state_dict(), state_dict_file)

In [5]:
GENRE_DATA_DIR = '/home/mlepekhin/data/genre'
GPT_MODELS_DIR = '/home/mlepekhin/models/mini_gpt/'
LANG = 'ru'

In [ ]:
for train_text_file in tqdm.tqdm(listdir(pathjoin(GENRE_DATA_DIR, LANG))):
    label = train_text_file[:-4]
    train_gpt_generator(
        pathjoin(GENRE_DATA_DIR, LANG, train_text_file),
        pathjoin(GPT_MODELS_DIR, LANG, label)
    )

  0%|          | 0/10 [00:00<?, ?it/s]

data has 745066 characters, 184 unique.



  0%|          | 0/1455 [00:00<?, ?it/s]/home/mlepekhin/anaconda3/envs/mlepekhin_research/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '

epoch 1 iter 0: train loss 5.34787. lr 5.999999e-04:   0%|          | 0/1455 [00:07<?, ?it/s]
epoch 1 iter 0: train loss 5.34787. lr 5.999999e-04:   0%|          | 1/1455 [00:07<2:59:08,  7.39s/it]
epoch 1 iter 1: train loss 3.88315. lr 5.999994e-04:   0%|          | 1/1455 [00:07<2:59:08,  7.39s/it]
epoch 1 iter 1: train loss 3.88315. lr 5.999994e-04:   0%|          | 2/1455 [00:07<2:07:49,  5.28s/it]
epoch 1 iter 2: train loss 3.94659. lr 5.999986e-04:   0%|          | 2/1455 [00:08<2:07:49,  5.28s/it]
epoch 1 iter 2: train loss 3.94659. lr 5.999986e-04:   0%|          | 3/1455 [00:08<1:31:51,  3.80s/it]
epoch 1 iter 3: train loss 3.460

epoch 1 iter 36: train loss 2.71652. lr 5.997627e-04:   3%|▎         | 37/1455 [00:19<07:51,  3.01it/s]
epoch 1 iter 37: train loss 2.71328. lr 5.997496e-04:   3%|▎         | 37/1455 [00:20<07:51,  3.01it/s]
epoch 1 iter 37: train loss 2.71328. lr 5.997496e-04:   3%|▎         | 38/1455 [00:20<07:46,  3.04it/s]
epoch 1 iter 38: train loss 2.71492. lr 5.997362e-04:   3%|▎         | 38/1455 [00:20<07:46,  3.04it/s]
epoch 1 iter 38: train loss 2.71492. lr 5.997362e-04:   3%|▎         | 39/1455 [00:20<07:42,  3.06it/s]
epoch 1 iter 39: train loss 2.69224. lr 5.997225e-04:   3%|▎         | 39/1455 [00:20<07:42,  3.06it/s]
epoch 1 iter 39: train loss 2.69224. lr 5.997225e-04:   3%|▎         | 40/1455 [00:20<07:40,  3.07it/s]
epoch 1 iter 40: train loss 2.69743. lr 5.997084e-04:   3%|▎         | 40/1455 [00:20<07:40,  3.07it/s]
epoch 1 iter 40: train loss 2.69743. lr 5.997084e-04:   3%|▎         | 41/1455 [00:20<07:38,  3.09it/s]
epoch 1 iter 41: train loss 2.70664. lr 5.996939e-04:   3%|▎    

epoch 1 iter 74: train loss 2.61741. lr 5.990211e-04:   5%|▌         | 75/1455 [00:32<07:28,  3.08it/s]
epoch 1 iter 75: train loss 2.61303. lr 5.989947e-04:   5%|▌         | 75/1455 [00:32<07:28,  3.08it/s]
epoch 1 iter 75: train loss 2.61303. lr 5.989947e-04:   5%|▌         | 76/1455 [00:32<07:27,  3.08it/s]
epoch 1 iter 76: train loss 2.60827. lr 5.989681e-04:   5%|▌         | 76/1455 [00:32<07:27,  3.08it/s]
epoch 1 iter 76: train loss 2.60827. lr 5.989681e-04:   5%|▌         | 77/1455 [00:32<07:27,  3.08it/s]
epoch 1 iter 77: train loss 2.60747. lr 5.989411e-04:   5%|▌         | 77/1455 [00:33<07:27,  3.08it/s]
epoch 1 iter 77: train loss 2.60747. lr 5.989411e-04:   5%|▌         | 78/1455 [00:33<07:41,  2.99it/s]
epoch 1 iter 78: train loss 2.59457. lr 5.989137e-04:   5%|▌         | 78/1455 [00:33<07:41,  2.99it/s]
epoch 1 iter 78: train loss 2.59457. lr 5.989137e-04:   5%|▌         | 79/1455 [00:33<07:36,  3.01it/s]
epoch 1 iter 79: train loss 2.60484. lr 5.988860e-04:   5%|▌    

...

epoch 1 iter 565: train loss 1.47430. lr 3.782551e-04:  83%|████████▎ | 565/681 [04:11<00:53,  2.18it/s]
epoch 1 iter 565: train loss 1.47430. lr 3.782551e-04:  83%|████████▎ | 566/681 [04:11<00:52,  2.19it/s]
epoch 1 iter 566: train loss 1.49516. lr 3.775860e-04:  83%|████████▎ | 566/681 [04:11<00:52,  2.19it/s]
epoch 1 iter 566: train loss 1.49516. lr 3.775860e-04:  83%|████████▎ | 567/681 [04:11<00:51,  2.20it/s]
epoch 1 iter 567: train loss 1.48078. lr 3.769165e-04:  83%|████████▎ | 567/681 [04:11<00:51,  2.20it/s]
epoch 1 iter 567: train loss 1.48078. lr 3.769165e-04:  83%|████████▎ | 568/681 [04:11<00:50,  2.22it/s]
epoch 1 iter 568: train loss 1.47965. lr 3.762466e-04:  83%|████████▎ | 568/681 [04:12<00:50,  2.22it/s]
epoch 1 iter 568: train loss 1.47965. lr 3.762466e-04:  84%|████████▎ | 569/681 [04:12<00:50,  2.21it/s]
epoch 1 iter 569: train loss 1.46787. lr 3.755762e-04:  84%|████████▎ | 569/681 [04:12<00:50,  2.21it/s]
epoch 1 iter 569: train loss 1.46787. lr 3.755762e-04: 

epoch 1 iter 602: train loss 1.41995. lr 3.532503e-04:  89%|████████▊ | 603/681 [04:27<00:34,  2.26it/s]
epoch 1 iter 603: train loss 1.42045. lr 3.525683e-04:  89%|████████▊ | 603/681 [04:27<00:34,  2.26it/s]
epoch 1 iter 603: train loss 1.42045. lr 3.525683e-04:  89%|████████▊ | 604/681 [04:27<00:33,  2.27it/s]
epoch 1 iter 604: train loss 1.40227. lr 3.518859e-04:  89%|████████▊ | 604/681 [04:28<00:33,  2.27it/s]
epoch 1 iter 604: train loss 1.40227. lr 3.518859e-04:  89%|████████▉ | 605/681 [04:28<00:33,  2.27it/s]
epoch 1 iter 605: train loss 1.41094. lr 3.512034e-04:  89%|████████▉ | 605/681 [04:28<00:33,  2.27it/s]
epoch 1 iter 605: train loss 1.41094. lr 3.512034e-04:  89%|████████▉ | 606/681 [04:28<00:32,  2.28it/s]
epoch 1 iter 606: train loss 1.40605. lr 3.505205e-04:  89%|████████▉ | 606/681 [04:28<00:32,  2.28it/s]
epoch 1 iter 606: train loss 1.40605. lr 3.505205e-04:  89%|████████▉ | 607/681 [04:28<00:31,  2.37it/s]
epoch 1 iter 607: train loss 1.40379. lr 3.498374e-04: 

epoch 1 iter 640: train loss 1.34538. lr 3.271668e-04:  94%|█████████▍| 640/681 [04:43<00:19,  2.05it/s]
epoch 1 iter 640: train loss 1.34538. lr 3.271668e-04:  94%|█████████▍| 641/681 [04:43<00:19,  2.03it/s]
epoch 1 iter 641: train loss 1.35363. lr 3.264767e-04:  94%|█████████▍| 641/681 [04:43<00:19,  2.03it/s]
epoch 1 iter 641: train loss 1.35363. lr 3.264767e-04:  94%|█████████▍| 642/681 [04:43<00:19,  2.02it/s]
epoch 1 iter 642: train loss 1.35444. lr 3.257864e-04:  94%|█████████▍| 642/681 [04:44<00:19,  2.02it/s]
epoch 1 iter 642: train loss 1.35444. lr 3.257864e-04:  94%|█████████▍| 643/681 [04:44<00:19,  1.97it/s]
epoch 1 iter 643: train loss 1.33767. lr 3.250961e-04:  94%|█████████▍| 643/681 [04:44<00:19,  1.97it/s]
epoch 1 iter 643: train loss 1.33767. lr 3.250961e-04:  95%|█████████▍| 644/681 [04:44<00:18,  2.01it/s]
epoch 1 iter 644: train loss 1.32678. lr 3.244055e-04:  95%|█████████▍| 644/681 [04:45<00:18,  2.01it/s]
epoch 1 iter 644: train loss 1.32678. lr 3.244055e-04: 

epoch 1 iter 677: train loss 1.27727. lr 3.015671e-04: 100%|█████████▉| 678/681 [05:00<00:01,  2.57it/s]
epoch 1 iter 678: train loss 1.26762. lr 3.008742e-04: 100%|█████████▉| 678/681 [05:00<00:01,  2.57it/s]
epoch 1 iter 678: train loss 1.26762. lr 3.008742e-04: 100%|█████████▉| 679/681 [05:00<00:00,  2.55it/s]
epoch 1 iter 679: train loss 1.27348. lr 3.001813e-04: 100%|█████████▉| 679/681 [05:01<00:00,  2.55it/s]
epoch 1 iter 679: train loss 1.27348. lr 3.001813e-04: 100%|█████████▉| 680/681 [05:01<00:00,  2.50it/s]
epoch 1 iter 680: train loss 1.28421. lr 3.000541e-04: 100%|█████████▉| 680/681 [05:01<00:00,  2.50it/s]
epoch 1 iter 680: train loss 1.28421. lr 3.000541e-04: 100%|██████████| 681/681 [05:01<00:00,  2.26it/s]

  0%|          | 0/681 [00:00<?, ?it/s]
epoch 2 iter 0: train loss 1.27188. lr 2.993612e-04:   0%|          | 0/681 [00:00<?, ?it/s]
epoch 2 iter 0: train loss 1.27188. lr 2.993612e-04:   0%|          | 1/681 [00:00<05:38,  2.01it/s]
epoch 2 iter 1: train loss 1.2

epoch 2 iter 35: train loss 1.20290. lr 2.751386e-04:   5%|▌         | 35/681 [00:15<04:36,  2.34it/s]
epoch 2 iter 35: train loss 1.20290. lr 2.751386e-04:   5%|▌         | 36/681 [00:15<04:37,  2.32it/s]
epoch 2 iter 36: train loss 1.20280. lr 2.744482e-04:   5%|▌         | 36/681 [00:16<04:37,  2.32it/s]
epoch 2 iter 36: train loss 1.20280. lr 2.744482e-04:   5%|▌         | 37/681 [00:16<04:33,  2.35it/s]
epoch 2 iter 37: train loss 1.21785. lr 2.737579e-04:   5%|▌         | 37/681 [00:16<04:33,  2.35it/s]
epoch 2 iter 37: train loss 1.21785. lr 2.737579e-04:   6%|▌         | 38/681 [00:16<04:32,  2.36it/s]
epoch 2 iter 38: train loss 1.21175. lr 2.730677e-04:   6%|▌         | 38/681 [00:16<04:32,  2.36it/s]
epoch 2 iter 38: train loss 1.21175. lr 2.730677e-04:   6%|▌         | 39/681 [00:16<04:31,  2.36it/s]
epoch 2 iter 39: train loss 1.20261. lr 2.723777e-04:   6%|▌         | 39/681 [00:17<04:31,  2.36it/s]
epoch 2 iter 39: train loss 1.20261. lr 2.723777e-04:   6%|▌         | 40